### Registering tables in the catalog 

Our catalog is created and we can start registering tables in it.

#### First of all, let's activate our catalog.
We will be repeating this command in following notebooks.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

21:56:18 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


21:56:18 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:56:18 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:56:18 | INFO     | No catalog activated.


21:56:19 | INFO     | 6 feature lists, 31 features deployed


...

21:56:19 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


21:56:19 | WARNING  | Remote SDK version (0.5.0.dev6) is different from local (0.5.0.dev1). Update local SDK to avoid unexpected behavior.


21:56:19 | INFO     | No catalog activated.


21:56:20 | INFO     | 6 feature lists, 31 features deployed


21:56:21 | INFO     | Catalog activated: Grocery Dataset Tutorial


#### Get data source 

To be able to get source tables from the data warehouse we need to get data source, which our catalog has access to. 

This data source contains collection of tables in our database, and we can use it to explore our DB schema:

In [2]:
ds = catalog.get_data_source()

Here we see we have access to a number of databases. For these tutorials we will use the one called 'TUTORIAL_DATASETS' with 4 different schemas in it. 

In [3]:
ds.list_databases()

['SNOWFLAKE', 'SNOWFLAKE_SAMPLE_DATA', 'TUTORIAL', 'TUTORIAL_DATASETS']

In [4]:
database_name = 'TUTORIAL_DATASETS'
ds.list_schemas(database_name=database_name)

['CREDITCARD', 'GROCERY', 'HEALTHCARE', 'INFORMATION_SCHEMA']

In [5]:
schema_name = 'GROCERY'
ds.list_source_tables(database_name=database_name, schema_name=schema_name)

['GROCERYPRODUCT', 'GROCERYCUSTOMER', 'GROCERYINVOICE', 'INVOICEITEMS']

#### Get source tables
We identified database and schema we want to work with, it is time to get source tables and register them in the catalog. 

In [6]:
customer_source_table = ds.get_source_table(
    database_name=database_name,
    schema_name=schema_name,
    table_name="GROCERYCUSTOMER"
)
invoice_source_table = ds.get_source_table(
    database_name=database_name,
    schema_name=schema_name,
    table_name="GROCERYINVOICE"
)
items_source_table = ds.get_source_table(
    database_name=database_name,
    schema_name=schema_name,
    table_name="INVOICEITEMS"
)
product_source_table = ds.get_source_table(
    database_name=database_name,
    schema_name=schema_name,
    table_name="GROCERYPRODUCT"
)

#### Registering Tables in the Catalog


This step, though slightly more intricate than our previous actions, is vital for our subsequent feature engineering tasks.

For accurate feature derivation, FeatureByte needs to understand the 'roles' of various tables.

We categorize tables into four types:

- Event tables - These capture distinct business events occurring at specific moments. An example would be customer invoices, specifically, the "Grocery Invoice" in our scenario.
- Item tables - These delve into the specifics about an event, such as the products a customer purchased. In our context, this is represented by "Invoice Items".
- Slowly Changing Dimension tables - These denote data similar to dimensions but may evolve over time. For instance, customers might shift addresses or update other details. In our use case, this is the "Grocery Customer".
- Dimension tables - These tables contain unchanging descriptive data, like information on particular products retailed in a store, exemplified by "Grocery Product" in our setting.

Feel free to explore [more on tables and table types](https://docs.featurebyte.com/latest/about/glossary/#related-to-tables), but at this point understanding just basic differences is more than enough. 

Let's register each table using respective type:

In [7]:
customer_table = customer_source_table.create_scd_table(
    name="GROCERYCUSTOMER",
    surrogate_key_column='RowID',
    natural_key_column="GroceryCustomerGuid",
    effective_timestamp_column="ValidFrom",
    current_flag_column ="CurrentRecord",
    record_creation_timestamp_column="record_available_at"
)
invoice_table = invoice_source_table.create_event_table(   
    name="GROCERYINVOICE",
    event_id_column="GroceryInvoiceGuid",
    event_timestamp_column="Timestamp",
    event_timestamp_timezone_offset_column="tz_offset",
    record_creation_timestamp_column="record_available_at"
)
items_table = items_source_table.create_item_table(
    name="INVOICEITEMS",
    event_id_column="GroceryInvoiceGuid",
    item_id_column="GroceryInvoiceItemGuid",
    event_table_name="GROCERYINVOICE",
    record_creation_timestamp_column="record_available_at"    
)
product_table = product_source_table.create_dimension_table(
    name="GROCERYPRODUCT",
    dimension_id_column="GroceryProductGuid"
)

After this we will be able to see our tables in the catalog:

In [8]:
display(catalog.list_tables())

id             name             type        status  \
0  64ff1c940d5bfbfb21bce78c   GROCERYPRODUCT  dimension_table  PUBLIC_DRAFT   
1  64ff1c920d5bfbfb21bce78b     INVOICEITEMS       item_table  PUBLIC_DRAFT   
2  64ff1c910d5bfbfb21bce78a   GROCERYINVOICE      event_table  PUBLIC_DRAFT   
3  64ff1c8f0d5bfbfb21bce789  GROCERYCUSTOMER        scd_table  PUBLIC_DRAFT   

  entities                  created_at  
0       []  2023-09-11T13:56:37.144000  
1       []  2023-09-11T13:56:35.927000  
2       []  2023-09-11T13:56:34.182000  
3       []  2023-09-11T13:56:32.993000

#### Initialize feature job settings

The last step we need to tackle is setting up the feature job settings.

Essentially, these settings determine when and how frequently we want to update the feature store. It also sets a 'blind spot' period, which is the time gap between when a feature is computed and the latest available event.

For instance, in our grocery context, if we aim to predict customer spending for the upcoming two weeks, we might consider using all of their invoices up to the present. However, our data pipeline may not capture the most recent invoices immediately due to the time required for data collection from edge devices, processing through ETL, and other steps. If we base our predictions on data up to a certain point, our production scenario might not be accurately represented, leading to poor prediction accuracy.

Lukily, featurebyte is smart enough to compute those settings for us:

In [9]:
invoice_table.initialize_default_feature_job_setting()

Working... |                                        | ▁▃▅ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▂▄▆ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▃▅▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▄▆█ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▅▇▇ 0% in 0s (~0s, 0.0%/s)

...

Working... |████████████████████████████████████████| ▁▃▅ 100% in 10s (~0s, 0.1%

Working... |████████████████████████████████████████| ▂▄▆ 100% in 10s (~0s, 0.1%

Working... |████████████████████████████████████████| ▃▅▇ 100% in 10s (~0s, 0.1%

Working... |████████████████████████████████████████| ▄▆█ 100% in 10s (~0s, 0.1%

Done! |████████████████████████████████████████| 100% in 10.3s (0.10%/s)        

You can always override default feature job settings, see [update_default_feature_job_setting](https://docs.featurebyte.com/latest/reference/featurebyte.api.event_table.EventTable.update_default_feature_job_setting/).


That's it for this tutorial, now we are ready for modeling our entities. 

### More details about concepts we discussed in this tutorial:
- [Data sources and source tables](https://docs.featurebyte.com/latest/about/glossary/#related-to-data-in-a-data-warehouse)
- [Tables in FeatureByte](https://docs.featurebyte.com/latest/about/glossary/#table)
- [Feature jobs](https://docs.featurebyte.com/latest/about/glossary/#related-to-feature-jobs)
- [Feature job settings](https://docs.featurebyte.com/latest/about/glossary/#feature-job-setting)

#### SDK reference for
- [DataSource](https://docs.featurebyte.com/latest/reference/core/data_source/)
- [Table](https://docs.featurebyte.com/latest/reference/core/table/)